# FeatureSelection

In [1]:

#importing libraries
from sklearn.datasets import load_boston
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import statsmodels.api as sm
%matplotlib inline
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import RFE
from sklearn.linear_model import RidgeCV, LassoCV, Ridge, Lasso

In [2]:
df = pd.read_csv("..\..\Project_DATA\HealthCareCat_flat_1.csv")

In [3]:
df.head()

State_County_CD  AGE  SEX  race  CCS101  CCS104  CCS105  CCS106  CCS108  \
0            22070   67    1     1       0       0       0       1       0   
1            22150   67    1     1       4       4       0       0       0   
2            22160   53    1     1      14       0      16       2       0   
3            22040   67    2     1       0       0       0       0       0   
4            22090   67    1     1       0       0       0      36       3   

   CCS257  ...  HCC154  HCC155  HCC157  HCC158  HCC161  HCC164  HCC174  \
0       0  ...       0       0       0       0       0       0       0   
1       0  ...       0       0       0       0       0       0       0   
2       1  ...       0       0       0       0       0       0       0   
3       0  ...       0       0       0       0       0       0       0   
4       1  ...       0       0       0       0       0       0       0   

   HCC176  HCC177  Spending_Cat  
0       0       0             1  
1       0       0             1  
2       0       0             1  
3       0       0             1  
4       0       0             1  

[5 rows x 356 columns]

#### The dataframe I have is very imbalanced :
#### df[df.Spending_Cat == 1] -- 125309
#### df[df.Spending_Cat == 2] -- 4719  --   x 25
#### df[df.Spending_Cat == 3] -- 1075  --   x 115
#### df[df.Spending_Cat == 4] -- 170   --   x 736
#### I will split it to train, dev and test now, before i starting feature selection process. This way test set will not be changed by over-sampling 

In [4]:
from sklearn.model_selection import train_test_split

df_train, df_test = train_test_split(df, test_size=0.2)

df_test.to_csv("..\..\Project_DATA\HealthCareCat_Test.csv", index=False)


In [5]:
X = df_train.drop("Spending_Cat",1)   #Feature Matrix
y = df_train["Spending_Cat"]          #Target Variable

#### Use Synthetic Minority Oversampling Technique to make dataset balanced

In [6]:

from imblearn.over_sampling import SMOTE

oversample = SMOTE()
X, y = oversample.fit_resample(X, y)


In [7]:
X["Spending_Cat"] = y
### Oversampled dataset split to train and dev and save as csv files
df_train, df_dev = train_test_split(X, test_size=0.2)
df_dev.to_csv("..\..\Project_DATA\HealthCareCat_Dev.csv", index=False)
df_train.to_csv("..\..\Project_DATA\HealthCareCat_Train.csv", index=False)

In [7]:
### read presaved results if exists

### featuresVoting = pd.read_csv("..\..\Project_DATA\FeatureSelection_results.csv")

In [8]:
df_train = pd.read_csv("..\..\Project_DATA\HealthCareCat_Train.csv")
df_dev = pd.read_csv("..\..\Project_DATA\HealthCareCat_Dev.csv")

X_train = df_train.drop("Spending_Cat",1)   #Feature Matrix
y_train = df_train["Spending_Cat"]          #Target Variable

X_dev = df_dev.drop("Spending_Cat",1)   #Feature Matrix
y_dev = df_dev["Spending_Cat"]          #Target Variable

### Univariate Analysis: Corellation of outcome variable with all other variables:

In [23]:
### create voting table for feature selection

featuresVoting = pd.DataFrame(X_train.columns)

In [12]:
### make univariate analysis using tableone 

from tableone import TableOne
groupby = 'Spending_Cat'
mytable = TableOne(df_train, groupby=groupby, pval=True)


In [13]:
mytable

Grouped by Spending_Cat                                                                                    
                                             Missing         Overall              1              2              3              4 P-Value
n                                                             320748          80285          79984          80216          80263        
State_County_CD, n (%) 22000                       0     12749 (4.0)     5935 (7.4)     3155 (3.9)     1588 (2.0)     2071 (2.6)  <0.001
                       22001                               701 (0.2)                     308 (0.4)      180 (0.2)      213 (0.3)        
                       22002                               686 (0.2)                     315 (0.4)      184 (0.2)      187 (0.2)        
                       22003                               678 (0.2)                     275 (0.3)      198 (0.2)      205 (0.3)        
                       22004                               707 (0.2)                     298 (0.4)      208 (0.3)      201 (0.3)        
                       22005                               650 (0.2)                     260 (0.3)      187 (0.2)      203 (0.3)        
                       22006                               703 (0.2)                     280 (0.4)      210 (0.3)      213 (0.3)        
                       22007                               647 (0.2)                     270 (0.3)      181 (0.2)      196 (0.2)        
                       22008                               693 (0.2)                     306 (0.4)      194 (0.2)      193 (0.2)        
                       22009                               664 (0.2)                     291 (0.4)      188 (0.2)      185 (0.2)        
                       22010                              5366 (1.7)     2911 (3.6)     1138 (1.4)     1008 (1.3)      309 (0.4)        
                       22011                               874 (0.3)                     330 (0.4)      264 (0.3)      280 (0.3)        
                       22012                               862 (0.3)                     321 (0.4)      275 (0.3)      266 (0.3)        
                       22013                               899 (0.3)                     333 (0.4)      261 (0.3)      305 (0.4)        
                       22014                               827 (0.3)                     319 (0.4)      249 (0.3)      259 (0.3)        
                       22015                               878 (0.3)                     322 (0.4)      290 (0.4)      266 (0.3)        
                       22016                               878 (0.3)                     335 (0.4)      259 (0.3)      284 (0.4)        
                       22017                               887 (0.3)                     315 (0.4)      271 (0.3)      301 (0.4)        
                       22018                               921 (0.3)                     350 (0.4)      305 (0.4)      266 (0.3)        
                       22019                               932 (0.3)                     353 (0.4)      270 (0.3)      309 (0.4)        
                       22020                             17934 (5.6)    8217 (10.2)     4441 (5.6)     3096 (3.9)     2180 (2.7)        
                       22021                               952 (0.3)                     250 (0.3)      264 (0.3)      438 (0.5)        
                       22022                               911 (0.3)                     216 (0.3)      237 (0.3)      458 (0.6)        
                       22023                               892 (0.3)                     228 (0.3)      246 (0.3)      418 (0.5)        
                       22024                               999 (0.3)                     247 (0.3)      276 (0.3)      476 (0.6)        
                       22025                               971 (0.3)                     269 (0.3)      283 (0.4)      419 (0.5)        
                       22026                            

In [25]:
### The tableone results say that almost all the features have a significant p-value (< 0.05). It followed with warning message 
### about possible invalid measurements, So I prefer to perform chi-square tests for every feature. 

from scipy import stats

featuresVoting["Univariable"] = 0
pvalues = []


rows, cols = X_train.shape
features = list(X_train.columns)
for i in range(cols):
    crosstab = pd.crosstab(y_train, X_train[features[i]])
    curr_pvalue = stats.chi2_contingency(crosstab)[1]
    pvalues.append(1 if curr_pvalue < 0.05 else 0)    
featuresVoting["Univariable"] = pvalues


In [26]:
featuresVoting

0  Univariable
0    State_County_CD            1
1                AGE            1
2                SEX            1
3               race            1
4             CCS101            1
..               ...          ...
350           HCC161            1
351           HCC164            1
352           HCC174            1
353           HCC176            1
354           HCC177            1

[355 rows x 2 columns]

In [27]:
featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)

<>:1: DeprecationWarning: invalid escape sequence \.
<>:1: DeprecationWarning: invalid escape sequence \.
<ipython-input-27-8e628774b413>:1: DeprecationWarning: invalid escape sequence \.
  featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)


#### I got mostly the same p-values that way 

### Multivariate analysis: 


#### Lasso

In [29]:
reg = LassoCV()
reg.fit(X_train, y_train)
print("Best alpha using built-in LassoCV: %f" % reg.alpha_)
print("Best score using built-in LassoCV: %f" %reg.score(X_train, y_train))
coef = pd.Series(reg.coef_, index = X_train.columns)

Best alpha using built-in LassoCV: 0.025719
Best score using built-in LassoCV: 0.373614


In [30]:
featuresVoting['Lasso1'] = coef.values
featuresVoting.loc[featuresVoting['Lasso1'] != 0, 'Lasso'] = 1
featuresVoting.loc[featuresVoting['Lasso1'] == 0, 'Lasso'] = 0
featuresVoting.Lasso = pd.to_numeric(featuresVoting.Lasso, downcast='integer')
featuresVoting = featuresVoting.drop(['Lasso1'], axis=1)
featuresVoting.head()

0  Univariable  Lasso
0  State_County_CD            1      1
1              AGE            1      1
2              SEX            1      1
3             race            1      0
4           CCS101            1      1

In [31]:
print("Lasso picked " + str(sum(coef != 0)) + " variables and eliminated the other " +  str(sum(coef == 0)) + " variables")

Lasso picked 144 variables and eliminated the other 211 variables


In [32]:
featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)

<>:1: DeprecationWarning: invalid escape sequence \.
<>:1: DeprecationWarning: invalid escape sequence \.
<ipython-input-32-8e628774b413>:1: DeprecationWarning: invalid escape sequence \.
  featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)


#### Random Forest

In [33]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel

sel = SelectFromModel(RandomForestClassifier(n_estimators = 100))
sel.fit(X_train, y_train)


SelectFromModel(estimator=RandomForestClassifier())

In [34]:
rf_sup = sel.get_support()

In [35]:
featuresVoting['RF'] = rf_sup.tolist()
featuresVoting['RF'] = featuresVoting['RF'].astype(int)

featuresVoting.head()

0  Univariable  Lasso  RF
0  State_County_CD            1      1   1
1              AGE            1      1   1
2              SEX            1      1   1
3             race            1      0   1
4           CCS101            1      1   1

In [36]:
featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)

<>:1: DeprecationWarning: invalid escape sequence \.
<>:1: DeprecationWarning: invalid escape sequence \.
<ipython-input-36-8e628774b413>:1: DeprecationWarning: invalid escape sequence \.
  featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)


#### Gradient Boost

In [37]:
from sklearn.ensemble import GradientBoostingClassifier

gbc = GradientBoostingClassifier(n_estimators=100, learning_rate=0.3, max_depth=10, random_state=0)
gbc.fit(X_train, y_train)


GradientBoostingClassifier(learning_rate=0.3, max_depth=10, random_state=0)

In [38]:
# feature importance
gb_imp = gbc.feature_importances_

In [39]:
featuresVoting['GradientBoost1'] = gb_imp.tolist()
featuresVoting.loc[featuresVoting['GradientBoost1'] != 0, 'GradientBoost'] = 1
featuresVoting.loc[featuresVoting['GradientBoost1'] == 0, 'GradientBoost'] = 0
featuresVoting.GradientBoost = pd.to_numeric(featuresVoting.GradientBoost, downcast='integer')
featuresVoting = featuresVoting.drop(['GradientBoost1'], axis=1)
featuresVoting.head()

0  Univariable  Lasso  RF  GradientBoost
0  State_County_CD            1      1   1              1
1              AGE            1      1   1              1
2              SEX            1      1   1              1
3             race            1      0   1              1
4           CCS101            1      1   1              1

In [40]:
featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)

<>:1: DeprecationWarning: invalid escape sequence \.
<>:1: DeprecationWarning: invalid escape sequence \.
<ipython-input-40-8e628774b413>:1: DeprecationWarning: invalid escape sequence \.
  featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)


#### SVM

In [21]:
# from sklearn import svm

# svm = svm.LinearSVC()
# svm.fit(X_train, y_train)

from sklearn.svm import LinearSVC
from sklearn.datasets import load_iris
from sklearn.feature_selection import SelectFromModel
svm = LinearSVC(C=0.01, penalty="l1", dual=False, max_iter=10000).fit(X_train, y_train)


In [22]:
pd.Series(abs(svm.coef_[0]), index=X_train.columns).nlargest(100)

HCC18      1.325324
HCC17      1.024352
HCC16      0.994149
HCC1       0.912624
HCC27      0.882052
             ...   
CCS2617    0.029521
CCS54      0.029068
CCS129     0.028966
CCS116     0.028850
CCS20      0.028809
Length: 100, dtype: float64

In [23]:
featuresVoting['SVM1'] = pd.Series(abs(svm.coef_[0]), index=X.columns).values

featuresVoting.loc[featuresVoting['SVM1'] > 0.5, 'SVM'] = 1
featuresVoting.loc[featuresVoting['SVM1'] <= 0.5, 'SVM'] = 0
featuresVoting.SVM = pd.to_numeric(featuresVoting.SVM, downcast='integer')
featuresVoting = featuresVoting.drop(['SVM1'], axis=1)
featuresVoting.head()



0  Univariable  Lasso  RF  GradientBoost  SVM
0  State_County_CD            1      1   1              1    0
1              AGE            1      1   1              1    0
2              SEX            1      1   1              1    1
3             race            1      0   1              1    0
4           CCS101            1      1   1              1    0

In [24]:
featuresVoting.to_csv("..\..\Project_DATA\FeatureSelection_results.csv", index=False)

#### Selection based on voting:


In [25]:
featuresVoting["Sum"] = featuresVoting.Univariable + featuresVoting.Lasso + featuresVoting.RF + featuresVoting.GradientBoost + featuresVoting.SVM
featuresVoting.sort_values(by='Sum', ascending=False)

0  Univariable  Lasso  RF  GradientBoost  SVM  Sum
2                SEX            1      1   1              1    1    5
293            HCC10            1      1   1              1    1    5
298            HCC19            1      1   1              1    1    5
0    State_County_CD            1      1   1              1    0    4
81            CCS237            1      1   1              1    0    4
..               ...          ...    ...  ..            ...  ...  ...
248           CCS189            1      0   0              0    0    1
266           CCS180            0      0   0              0    0    0
277           CCS194            0      0   0              0    0    0
285           CCS218            0      0   0              0    0    0
286          CCS2602            0      0   0              0    0    0

[355 rows x 7 columns]

In [26]:
featuresInfluent =  featuresVoting[featuresVoting['Sum'] > 3]
featuresInfluent

0  Univariable  Lasso  RF  GradientBoost  SVM  Sum
0    State_County_CD            1      1   1              1    0    4
1                AGE            1      1   1              1    0    4
2                SEX            1      1   1              1    1    5
4             CCS101            1      1   1              1    0    4
5             CCS104            1      1   1              1    0    4
..               ...          ...    ...  ..            ...  ...  ...
185           CCS231            1      1   1              1    0    4
200            CCS45            1      1   1              1    0    4
207            CCS39            1      1   1              1    0    4
293            HCC10            1      1   1              1    1    5
298            HCC19            1      1   1              1    1    5

[94 rows x 7 columns]

In [27]:
featuresInfluent.to_csv("..\..\Project_DATA\SelectedFeatures.csv", index=False)